### Qwen2.5-7B-Instruct LLM run on Aristotle pipeline
### This is run in Runpod/remote Jupyter environment

In [1]:
!pip install transformers safetensors sentencepiece huggingface-hub accelerate bitsandbytes tqdm openai backoff retrying protobuf

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 12.0/12.0 MB 49.6 MB/s  0:00:00eta 0:00:01
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 564.3/564.3 kB 46.9 MB/s  0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 3.2/3.2 MB 67.4 MB/s  0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 3.3/3.3 MB 67.4 MB/s  0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.4/1.4 MB 59.0 MB/s  0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 60.1/60.1 MB 79.9 MB/s  0:00:00 eta 0:00:01
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.0/1.0 MB 69.3 MB/s  0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 2.1/2.1 MB 75.0 MB/s  0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 803.4/803.4 kB 199.2 MB/s  0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 19/19 [accelerate]9 [bitsandbytes]ub]


In [2]:
!git lfs install
!git clone https://huggingface.co/Qwen/Qwen2.5-7B-Instruct LLM_MODELS/Qwen2.5-7B-Instruct

Git LFS initialized.
Cloning into 'LLM_MODELS/Qwen2.5-7B-Instruct'...
remote: Enumerating objects: 50, done.
remote: Counting objects: 100% (47/47), done.
remote: Compressing objects: 100% (47/47), done.
remote: Total 50 (delta 21), reused 0 (delta 0), pack-reused 3 (from 1)
Unpacking objects: 100% (50/50), 3.61 MiB | 6.06 MiB/s, done.
Filtering content: 100% (4/4), 14.18 GiB | 66.54 MiB/s, done.


In [3]:
import os
from pathlib import Path

os.environ["TOKENIZERS_PARALLELISM"] = "false"
######### Also useful to reduce thread contention:
os.environ["OMP_NUM_THREADS"] = "1"
os.environ["MKL_NUM_THREADS"] = "1"

snapshot_path = "/workspace/LLM_MODELS/Qwen2.5-7B-Instruct" ############## <--- Change this based on platform and models

os.environ["LOCAL_MODEL_PATH"] = snapshot_path
os.environ["LLM_MODEL"] = snapshot_path

######## enable 4-bit for quant (and bitsandbytes is set up)
os.environ["LLM_LOAD_IN_4BIT"] = "1"  # or "0" to disable quantization

print("LOCAL_MODEL_PATH =", os.environ["LOCAL_MODEL_PATH"])
print("LLM_MODEL =", os.environ["LLM_MODEL"])

LOCAL_MODEL_PATH = /workspace/LLM_MODELS/Qwen2.5-7B-Instruct
LLM_MODEL = /workspace/LLM_MODELS/Qwen2.5-7B-Instruct


In [4]:
#Test for Max Time generation stopping criteria
from llm_backends import HFBackend
hb = HFBackend(local_model_path=snapshot_path, quantize_4bit=True)
print("Calling short test (3s max_time)...")
res = hb.generate("Write a long list of words and sentences: ", max_new_tokens=1024, max_time=3.0)
print("Result length:", len(res))
print(res[:1000])

print("Calling short test (10s max_time)...")
res = hb.generate("Write a long list of words and sentences: ", max_new_tokens=1024, max_time=10.0)
print("Result length:", len(res))
print(res[:1000])

Loading checkpoint shards:   0%|          | 0/4 [00:00<?, ?it/s]

The following generation flags are not valid and may be ignored: ['temperature', 'top_k']. Set `TRANSFORMERS_VERBOSITY=info` for more details.


Calling short test (3s max_time)...
Result length: 375
Write a long list of words and sentences: 10 adjectives, 10 nouns, 10 verbs, 10 adverbs, 10 prepositions, 10 conjunctions, 10 pronouns, 10 exclamations.

Adjectives:
1. Beautiful
2. Smart
3. Kind
4. Clever
5. Brave
6. Strong
7. Happy
8. Silly
9. Curious
10. Wise

Nouns:
1. Cat
2. Car
3. Book
4. Sun
5. Moon
6. Star
7. Ocean
8. Sky
9. Tree
10. Flower

Verbs:
1. Run
2. Jump
3
Calling short test (10s max_time)...
Result length: 1557
Write a long list of words and sentences: 10 adjectives, 10 nouns, 10 verbs, 10 adverbs, 10 prepositions, 10 conjunctions, 10 pronouns, 10 exclamations.

Adjectives:
1. Beautiful
2. Smart
3. Kind
4. Clever
5. Brave
6. Strong
7. Happy
8. Silly
9. Curious
10. Wise

Nouns:
1. Cat
2. Car
3. Book
4. Sun
5. Moon
6. Star
7. Ocean
8. Sky
9. Tree
10. Flower

Verbs:
1. Run
2. Jump
3. Sing
4. Laugh
5. Cry
6. Eat
7. Sleep
8. Read
9. Write
10. Think

Adverbs:
1. Quickly
2. Slowly
3. Loudly
4. Quietly
5. Happily
6. Sadly

In [5]:
#!python run_pipeline.py --dataset_name ProntoQA --sample_pct 0 --batch_size 1
#print("\nFinished translating dataset\n")

In [ ]:
os.environ["LLM_WORKER_MAX_TIME"] = "450"  # Change this every process (translate, decompose, search_resolve), different time limit is needed in seconds.

# With original prompts
!python translate_to_fol.py --data_path manual_data_translated --dataset_name ProntoQA --sample_pct 100 --prompts_folder manual_prompts_translated --prompts_file translation --split dev --save_path results_translated/prompts_original --model_name $LLM_MODEL --batch_num 1 --max_new_tokens 6700

SAMPLE PCT: 100
Loaded 50 examples from dev split.
Loading translation file:  manual_prompts_translated/ProntoQA/translation.txt
Number of batch:  1
Translating...
Translation prompt_a:  Deskripsi Tugas: Anda diberikan sebuah deskripsi permasalahan dan pertanyaan. Tugasnya adalah:
1) parsing konteks menjadi aturan logika berdasarkan predikat yang ditentukan
2) jika konteks berbentuk plural, maka konteks tersebut juga harus diterjemahkan ke bentuk tunggal
3) menulis fakta yang disebutkan dalam masalah, dan pastikan mereka diterjemahkan dalam bentuk logika juga.
4) parsing konjektur ke dalam bentuk logika
5) berikan penanda ***Bentuk Akhir*** sebagai output akhir dari tugas Anda.
6) silakan berikan output akhir dalam format berikut. Pastikan Anda menerjemahkan dalam urutan berikut: fakta, aturan, kemudian konjektur.

------

Berikut adalah contohnya:
Konteks:
Setiap jompus memiliki sifat eksentris. Setiap jompus adalah wumpus. Setiap wumpus memiliki sifat tidak transparan. Wumpuses adala

In [ ]:
# With modified prompts
!python translate_to_fol.py --data_path manual_data_translated --dataset_name ProntoQA --sample_pct 100 --prompts_folder manual_prompts_translated --prompts_file translation_modified --split dev --save_path results_translated/prompts_modified --model_name $LLM_MODEL --batch_num 1 --max_new_tokens 6700

SAMPLE PCT: 100
Loaded 50 examples from dev split.
Loading translation file:  manual_prompts_translated/ProntoQA/translation_modified.txt
Number of batch:  1
Translating...
Translation prompt_a:  Deskripsi Tugas: Anda diberikan sebuah deskripsi permasalahan dan pertanyaan. Tugasnya adalah:
1) parsing konteks menjadi aturan logika berdasarkan predikat yang ditentukan
2) jika konteks berbentuk plural, maka konteks tersebut juga harus diterjemahkan ke bentuk tunggal
3) menulis fakta yang disebutkan dalam masalah, dan pastikan mereka diterjemahkan dalam bentuk logika juga.
4) parsing konjektur ke dalam bentuk logika
5) jangan mencoba menyelesaikan konjektur atau permasalahan, cukup melakukan perintah parsing yang dibutuhkan
6) berikan penanda ***Bentuk Akhir*** sebagai output akhir dari tugas Anda.
7) silakan berikan output akhir dalam format berikut. Pastikan Anda menerjemahkan dalam urutan berikut: fakta, aturan, kemudian konjektur.

------

Berikut adalah contohnya:
Konteks:
Setiap jomp

In [8]:
#!python negate.py --dataset_name ProntoQA --save_path results_translated --model_name /workspace/LLM_MODELS/Qwen2.5-7B-Instruct

In [9]:
#!python search_resolve.py --data_path manual_data_translate --dataset_name ProntoQA --prompts_folder manual_prompts_translated --split dev --save_path results_translated --model_name /workspace/LLM_MODELS/Qwen2.5-7B-Instruct --batch_num 1 --negation False --max_new_tokens 6700

In [10]:
#!python search_resolve.py --data_path manual_data_translate --dataset_name ProntoQA --prompts_folder manual_prompts_translated --split dev --save_path results_translated --model_name /workspace/LLM_MODELS/Qwen2.5-7B-Instruct --batch_num 1 --negation True --max_new_tokens 6700

In [11]:
#!python evaluate.py --dataset_name ProntoQA --save_path resulys_translated --model_name /workspace/LLM_MODELS/Qwen2.5-7B-Instruct